In [2]:
!pip install sentence-transformers

In [3]:
from sentence_transformers import SentenceTransformer, InputExample, losses, util
from torch.utils.data import DataLoader
import json
import pandas as pd
import sys

In [4]:
with open('/content/products.json', 'r') as file:
    products = json.load(file)

In [5]:
with open('/content/labels_synth_train.json', 'r') as file:
    labelsTrain = json.load(file)

In [6]:
with open('/content/queries_synth_train.json', 'r') as file:
    queriesTrain = json.load(file)

In [7]:
print(queriesTrain)

[{'query_id': 's334', 'query': 'hearty organic soups for dinner'}, {'query_id': 's255', 'query': 'versatile cut chicken for grilling'}, {'query_id': 's245', 'query': 'quick cook pork steaks'}, {'query_id': 's79', 'query': 'organic herbs and spices for chili'}, {'query_id': 's319', 'query': 'ready to eat spicy tamales'}, {'query_id': 's234', 'query': 'fragrance free wipes for babies'}, {'query_id': 's105', 'query': 'fiber rich breakfast cereal'}, {'query_id': 's268', 'query': 'high fiber breakfast granola'}, {'query_id': 's78', 'query': 'spicy chili powder for cooking'}, {'query_id': 's244', 'query': 'citrus seasoned pork for grilling'}, {'query_id': 's289', 'query': 'high protein pasta salad for lunch'}, {'query_id': 's309', 'query': 'scented wax melts for air freshening'}, {'query_id': 's514', 'query': 'dolphin-safe tuna for salads'}, {'query_id': 's302', 'query': 'Colby cheese for sandwiches'}, {'query_id': 's415', 'query': 'vegan frozen desserts'}, {'query_id': 's372', 'query': 'USD

In [8]:
print(labelsTrain)

[{'query_id': 's118', 'product_id': '8321001', 'relevance': 3}, {'query_id': 's118', 'product_id': '8320001', 'relevance': 0}, {'query_id': 's118', 'product_id': '1523188', 'relevance': 0}, {'query_id': 's118', 'product_id': '1993851', 'relevance': 0}, {'query_id': 's118', 'product_id': '1993857', 'relevance': 0}, {'query_id': 's118', 'product_id': '5130013', 'relevance': 0}, {'query_id': 's118', 'product_id': '646991', 'relevance': 0}, {'query_id': 's118', 'product_id': '646993', 'relevance': 0}, {'query_id': 's118', 'product_id': '5697034', 'relevance': 0}, {'query_id': 's118', 'product_id': '5156577', 'relevance': 0}, {'query_id': 's118', 'product_id': '11253055', 'relevance': 0}, {'query_id': 's118', 'product_id': '3751166', 'relevance': 0}, {'query_id': 's118', 'product_id': '5697031', 'relevance': 0}, {'query_id': 's118', 'product_id': '608357', 'relevance': 0}, {'query_id': 's118', 'product_id': '1993855', 'relevance': 0}, {'query_id': 's118', 'product_id': '8321501', 'relevance

In [9]:
print(products)

[{'product_id': '10045036', 'title': 'H-E-B Fish Market Party Tray - Seasoned Shrimp Cocktail', 'description': "Before everyone comes over to your place, pick up this generous-sized party tray from our H-E-B Fish Market. It's made up of buttery, lemon dill seasoned shrimp and Chesapeake-style seasoned shrimp. And in the center, there's our signature blend of cocktail sauce for dipping, packed with a zesty tang unlike any other. For parties and special occasions, this platter is a definite crowd-pleaser.; Seasoned shrimp cocktail party tray; 12 buttery, lemon dill seasoned shrimp; 12 Chesapeake-style seasoned shrimp; Zesty, tangy cocktail sauce for dipping; Served with lemon wedges; Ready to eat; Great party platter; From our H-E-B Fish Market", 'brand': 'H-E-B', 'category_path': 'Meat & seafood -> Seafood -> Shrimp & shellfish', 'safety_warning': 'Contains: SHRIMP, MILK, ANCHOVY. Caution: CONTAINS SHELLS. Perishable. Keep refrigerated.', 'ingredients': 'shrimp (shrimp, water, salt), co

In [10]:
labelsTrain_df = pd.DataFrame(labelsTrain)
queriesTrain_df = pd.DataFrame(queriesTrain)
products_df = pd.DataFrame(products)

mergedData = labelsTrain_df.merge(queriesTrain_df, on="query_id").merge(products_df, on="product_id")

In [11]:
if 'product_text' not in mergedData.columns:
    print("Creating 'product_text' column for mergedData...")
    def create_product_text(row):
        return (
            f"Title: {row['title']}. "
            f"Brand: {row['brand']}. "
            f"Category: {row['category_path']}. "
            f"Description: {row['description']}. "
            f"Ingredients: {row['ingredients']}"
        )
    mergedData['product_text'] = mergedData.apply(create_product_text, axis=1)
    print("Done creating 'product_text' for mergedData.")

# Ensure products_df also has the 'product_text' column
if 'product_text' not in products_df.columns:
    print("Creating 'product_text' column for products_df...")
    products_df['product_text'] = products_df.apply(create_product_text, axis=1)
    print("Done creating 'product_text' for products_df.")

Creating 'product_text' column for mergedData...
Done creating 'product_text' for mergedData.
Creating 'product_text' column for products_df...
Done creating 'product_text' for products_df.


In [12]:
max_relevance = mergedData['relevance'].max()
mergedData['norm_relevance'] = mergedData['relevance'] / max_relevance

# Create InputExample objects
train_examples = []
for index, row in mergedData.iterrows():
    train_examples.append(
        InputExample(
            texts=[row['query'], row['product_text']],
            label=row['norm_relevance']
        )
    )

print(f"Created {len(train_examples)} training examples.")

Created 10974 training examples.


In [13]:
model = SentenceTransformer('all-MiniLM-L6-v2')

/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

README.md: 0.00B [00:00, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/350 [00:00<?, ?B/s]

vocab.txt: 0.00B [00:00, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

In [14]:
train_loss = losses.CosineSimilarityLoss(model)
train_dataloader = DataLoader(train_examples, shuffle=True, batch_size=32)

In [15]:
num_epochs = 3
warmup_steps = int(len(train_dataloader) * num_epochs * 0.1) # 10% of steps

print("Starting model training...")
model.fit(
    train_objectives=[(train_dataloader, train_loss)],
    epochs=num_epochs,
    warmup_steps=warmup_steps,
    output_path='./heb_retriever_model' # Path to save the trained model
)

print("Training complete. Model saved to './heb_retriever_model'.")

Starting model training...


Computing widget examples:   0%|          | 0/1 [00:00<?, ?example/s]

/usr/local/lib/python3.12/dist-packages/notebook/notebookapp.py:191: SyntaxWarning: invalid escape sequence '\/'
  | |_| | '_ \/ _` / _` |  _/ -_)
wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize?ref=models
wandb: Paste an API key from your profile and hit enter:

 ··········


wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: No netrc file found, creating one.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
wandb: Currently logged in as: malvika-koushik (malvika-koushik-texas-a-m-university) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


Training complete. Model saved to './heb_retriever_model'.


In [16]:
from sentence_transformers import SentenceTransformer, util

model = SentenceTransformer('./heb_retriever_model')
unique_products = products_df.drop_duplicates(subset=['product_id'])
product_texts = unique_products['product_text'].tolist()
product_ids = unique_products['product_id'].tolist()

print(f"Encoding {len(product_texts)} products...")
product_embeddings = model.encode(product_texts, convert_to_tensor=True, show_progress_bar=True)
print(f"Product embeddings shape: {product_embeddings.shape}")


user_query = "healthy snacks for kids"

print(f"\nSearching for: '{user_query}'")

query_embedding = model.encode(user_query, convert_to_tensor=True)
hits = util.semantic_search(query_embedding, product_embeddings, top_k=5)

hits = hits[0]

print("Top 5 results:")
for hit in hits:
    product_index = hit['corpus_id']
    score = hit['score']

    product_id = product_ids[product_index]
    product_title = unique_products.iloc[product_index]['title']

    print(f"  - Score: {score:.4f} \t ID: {product_id} \t Title: {product_title}")

Encoding 3287 products...


Batches:   0%|          | 0/103 [00:00<?, ?it/s]

Product embeddings shape: torch.Size([3287, 384])

Searching for: 'healthy snacks for kids'
Top 5 results:
  - Score: 0.5371 	 ID: 5568030 	 Title: Meal Simple by H-E-B Kids' Ham & Cheese Slider, Pretzels, Grapes, Cucumber & Ranch Dip
  - Score: 0.5094 	 ID: 5568029 	 Title: Meal Simple by H-E-B Kids' Half PB&J Sandwich, Apples, Pretzels, Carrots & Ranch
  - Score: 0.4979 	 ID: 5568022 	 Title: Meal Simple by H-E-B Kids' Turkey & Cheese Slider, Pretzels, Grapes & Cucumber
  - Score: 0.4907 	 ID: 5568038 	 Title: Meal Simple by H-E-B Kids' PB&J Sandwich, Pretzels, Orange, Carrots & Hummus
  - Score: 0.4750 	 ID: 3766710 	 Title: H-E-B Oatmeal Bars - Peanut Butter & Strawberry Jelly


In [17]:
print("Loading trained model...")
model = SentenceTransformer('./heb_retriever_model')

Loading trained model...


In [18]:
if 'product_text' not in products_df.columns:
    print("Creating 'product_text' column...")
    def create_product_text(row):
        return (
            f"Title: {row['title']}. "
            f"Brand: {row['brand']}. "
            f"Category: {row['category_path']}. "
            f"Description: {row['description']}. "
            f"Ingredients: {row['ingredients']}"
        )
    products_df['product_text'] = products_df.apply(create_product_text, axis=1)

In [19]:
unique_products = products_df.drop_duplicates(subset=['product_id'])
product_texts = unique_products['product_text'].tolist()
product_ids_list = unique_products['product_id'].tolist() # This list maps index -> product_id

print(f"Encoding {len(product_texts)} products for the vector index...")
product_embeddings = model.encode(product_texts, convert_to_tensor=True, show_progress_bar=True)
print("Product encoding complete.")

Encoding 3287 products for the vector index...


Batches:   0%|          | 0/103 [00:00<?, ?it/s]

Product encoding complete.


In [20]:
print("Loading test queries...")
try:
    with open('/content/queries_synth_test.json', 'r') as file:
        test_queries = json.load(file)
except FileNotFoundError:
    print("Error: /content/queries_synth_test.json not found.")
    # sys.exit("Stopping script.")
    test_queries = [] # Avoid crashing the rest of the example

Loading test queries...


In [21]:
TOP_K_RESULTS = 30

submission_list = []
print(f"Generating rankings for {len(test_queries)} test queries...")

Generating rankings for 191 test queries...


In [22]:
for test_query in test_queries:
    query_id = test_query['query_id']
    query_text = test_query['query']

    query_embedding = model.encode(query_text, convert_to_tensor=True)

    hits = util.semantic_search(query_embedding, product_embeddings, top_k=TOP_K_RESULTS)
    hits = hits[0]

    for rank, hit in enumerate(hits, start=1):
        product_index = hit['corpus_id']
        product_id = product_ids_list[product_index]

        submission_entry = {
            "query_id": query_id,
            "rank": rank,
            "product_id": product_id
        }
        submission_list.append(submission_entry)

print(f"Generated {len(submission_list)} total ranking entries.")

Generated 5730 total ranking entries.


In [23]:
print(len(submission_list))

5730


In [24]:
print("Saving submission.json...")
with open('submission.json', 'w') as f:
    # Use indent=2 for a readable, formatted file
    json.dump(submission_list, f, indent=2)

print("\nAll done! 'submission.json' has been created.")

Saving submission.json...

All done! 'submission.json' has been created.


-----------------------